In [8]:
import pandas as pd
from numpy import nan
import pandas_gbq
import matplotlib as mpl
import pydeck as pdk
import json

In [2]:
query = """SELECT *
    FROM datario.adm_cor_comando.ocorrencias
    WHERE data_particao > DATE("2023-06-01")""" # Coloquei um limite pra não gastar 3GB do google quando for puxar
chamados_rjcor = pandas_gbq.read_gbq(query, project_id = "hackaton-fgv")
chamados_rjcor

/home/pedro/Modelos/Faculdade/hackaton-fgv/venv/lib/python3.11/site-packages/google/auth/_default.py:76: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK without a quota project. You might receive a "quota exceeded" or "API not enabled" error. See the following page for troubleshooting: https://cloud.google.com/docs/authentication/adc-troubleshooting/user-creds. 
  warnings.warn(_CLOUD_SDK_CREDENTIALS_WARNING)
/home/pedro/Modelos/Faculdade/hackaton-fgv/venv/lib/python3.11/site-packages/google/cloud/bigquery/table.py:2257: UserWarning: A progress bar was requested, but there was an error loading the tqdm library. Please install tqdm to use the progress bar functionality.
  record_batch = self.to_arrow(


id_pop id_evento                    bairro               data_inicio  \
0         1    105336           Barra da tijuca 2023-11-01 10:45:32+00:00   
1         1    105359                    Grajau 2023-11-01 17:32:55+00:00   
2         1    105316                 Guadalupe 2023-11-01 06:56:06+00:00   
3         1    105340                Água santa 2023-11-01 12:03:46+00:00   
4         1    105406           Barra da tijuca 2023-11-02 19:54:37+00:00   
...     ...       ...                       ...                       ...   
7385      1    102225             São cristóvão 2023-09-10 17:06:04+00:00   
7386      1    101768         Praca da bandeira 2023-09-01 05:49:09+00:00   
7387      1    102040  Freguesia de jacarepaguá 2023-09-06 08:56:24+00:00   
7388      1    102725  Freguesia de jacarepaguá 2023-09-19 10:29:30+00:00   
7389      2    103007  Freguesia de jacarepaguá 2023-09-25 07:44:30+00:00   

                      data_fim  prazo  \
0    2023-11-01 11:37:06+00:00  Curto   
1    2023-11-01 18:19:18+00:00  Curto   
2    2023-11-01 07:35:59+00:00  Curto   
3    2023-11-01 13:05:55+00:00  Curto   
4    2023-11-02 22:08:34+00:00  Curto   
...                        ...    ...   
7385 2023-09-10 17:25:41+00:00  Curto   
7386 2023-09-01 06:11:50+00:00  Curto   
7387 2023-09-06 09:13:36+00:00  Curto   
7388 2023-09-19 11:42:58+00:00  Curto   
7389 2023-09-25 08:28:33+00:00  Curto   

                                              descricao gravidade   latitude  \
0     Av. min. ivan lins - alt. ponte da joatinga - ...     Baixo -23.007138   
1     Estr. grajaú/jpa - alt. km 4,5 - eng. novo - s...     Baixo -22.923714   
2     Av. brasil - alt. guadalupe - guadalupe - sent...     Baixo -22.861892   
3           Linha amarela - alt. pedágio - sent. fundão     Baixo -22.908814   
4     Av. das américas - alt. n° 4059 - barra da tij...     Baixo -23.000598   
...                                                 ...       ...        ...   
7385  Viaduto do gasômetro - alt. rodoviária - santo...     Medio -22.898193   
7386  Elevado paulo de frontin  - rio comprido - sen...     Medio -22.919729   
7387        Linha amarela - cidade de deus - sent. orla     Medio -22.947957   
7388          Túnel rebouças - 2° galeria - sent. lagoa     Medio -22.949183   
7389          Túnel rebouças - 2a galeria - sent. lagoa     Medio -22.949183   

      longitude   status      tipo data_particao  
0    -43.305252  Fechado  Primario    2023-11-01  
1    -43.258467  Fechado  Primario    2023-11-01  
2    -43.549415  Fechado  Primario    2023-11-01  
3    -43.314814  Fechado  Primario    2023-11-01  
4    -43.354677  Fechado  Primario    2023-11-02  
...         ...      ...       ...           ...  
7385 -43.211672  Fechado  Primario    2023-09-10  
7386 -43.209590  Fechado  Primario    2023-09-01  
7387 -43.355575  Fechado  Primario    2023-09-06  
7388 -43.350800  Fechado  Primario    2023-09-19  
7389 -43.350800  Fechado  Primario    2023-09-25  

[7390 rows x 13 columns]

In [17]:
chamados_rjcor["data_inicio"] = pd.to_datetime(chamados_rjcor["data_inicio"])

In [9]:
chamados_rjcor["gravidade"].value_counts(dropna = False)

gravidade
Baixo     3864
Normal    2770
Medio      402
Média      339
Alta         8
None         4
Alto         3
Name: count, dtype: int64

In [10]:
gravidades = {
    "Normal": [255, 255, 0],
    "Média": [255, 165, 0],
    "Alta": [255, 0, 0],
    None: [120, 120, 120],
    "Baixo": [255, 255, 0],
    "Medio": [255, 165, 0],
    "Alto": [255, 0, 0]
}
chamados_rjcor["coloracao"] = chamados_rjcor.apply(lambda linha: gravidades[linha["gravidade"]], axis=1)
chamados_rjcor

id_pop id_evento                    bairro               data_inicio  \
0         1    105336           Barra da tijuca 2023-11-01 10:45:32+00:00   
1         1    105359                    Grajau 2023-11-01 17:32:55+00:00   
2         1    105316                 Guadalupe 2023-11-01 06:56:06+00:00   
3         1    105340                Água santa 2023-11-01 12:03:46+00:00   
4         1    105406           Barra da tijuca 2023-11-02 19:54:37+00:00   
...     ...       ...                       ...                       ...   
7385      1    102225             São cristóvão 2023-09-10 17:06:04+00:00   
7386      1    101768         Praca da bandeira 2023-09-01 05:49:09+00:00   
7387      1    102040  Freguesia de jacarepaguá 2023-09-06 08:56:24+00:00   
7388      1    102725  Freguesia de jacarepaguá 2023-09-19 10:29:30+00:00   
7389      2    103007  Freguesia de jacarepaguá 2023-09-25 07:44:30+00:00   

                      data_fim  prazo  \
0    2023-11-01 11:37:06+00:00  Curto   
1    2023-11-01 18:19:18+00:00  Curto   
2    2023-11-01 07:35:59+00:00  Curto   
3    2023-11-01 13:05:55+00:00  Curto   
4    2023-11-02 22:08:34+00:00  Curto   
...                        ...    ...   
7385 2023-09-10 17:25:41+00:00  Curto   
7386 2023-09-01 06:11:50+00:00  Curto   
7387 2023-09-06 09:13:36+00:00  Curto   
7388 2023-09-19 11:42:58+00:00  Curto   
7389 2023-09-25 08:28:33+00:00  Curto   

                                              descricao gravidade   latitude  \
0     Av. min. ivan lins - alt. ponte da joatinga - ...     Baixo -23.007138   
1     Estr. grajaú/jpa - alt. km 4,5 - eng. novo - s...     Baixo -22.923714   
2     Av. brasil - alt. guadalupe - guadalupe - sent...     Baixo -22.861892   
3           Linha amarela - alt. pedágio - sent. fundão     Baixo -22.908814   
4     Av. das américas - alt. n° 4059 - barra da tij...     Baixo -23.000598   
...                                                 ...       ...        ...   
7385  Viaduto do gasômetro - alt. rodoviária - santo...     Medio -22.898193   
7386  Elevado paulo de frontin  - rio comprido - sen...     Medio -22.919729   
7387        Linha amarela - cidade de deus - sent. orla     Medio -22.947957   
7388          Túnel rebouças - 2° galeria - sent. lagoa     Medio -22.949183   
7389          Túnel rebouças - 2a galeria - sent. lagoa     Medio -22.949183   

      longitude   status      tipo data_particao      coloracao  raio  
0    -43.305252  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
1    -43.258467  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
2    -43.549415  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
3    -43.314814  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
4    -43.354677  Fechado  Primario    2023-11-02  [255, 255, 0]    50  
...         ...      ...       ...           ...            ...   ...  
7385 -43.211672  Fechado  Primario    2023-09-10  [255, 165, 0]    50  
7386 -43.209590  Fechado  Primario    2023-09-01  [255, 165, 0]    50  
7387 -43.355575  Fechado  Primario    2023-09-06  [255, 165, 0]    50  
7388 -43.350800  Fechado  Primario    2023-09-19  [255, 165, 0]    50  
7389 -43.350800  Fechado  Primario    2023-09-25  [255, 165, 0]    50  

[7390 rows x 15 columns]

In [14]:
status = {
    "Fechado": 50,
    "Aberto":200
}
chamados_rjcor["raio"] = chamados_rjcor.apply(lambda linha: status[linha["status"]], axis=1)
chamados_rjcor

id_pop id_evento                    bairro               data_inicio  \
0         1    105336           Barra da tijuca 2023-11-01 10:45:32+00:00   
1         1    105359                    Grajau 2023-11-01 17:32:55+00:00   
2         1    105316                 Guadalupe 2023-11-01 06:56:06+00:00   
3         1    105340                Água santa 2023-11-01 12:03:46+00:00   
4         1    105406           Barra da tijuca 2023-11-02 19:54:37+00:00   
...     ...       ...                       ...                       ...   
7385      1    102225             São cristóvão 2023-09-10 17:06:04+00:00   
7386      1    101768         Praca da bandeira 2023-09-01 05:49:09+00:00   
7387      1    102040  Freguesia de jacarepaguá 2023-09-06 08:56:24+00:00   
7388      1    102725  Freguesia de jacarepaguá 2023-09-19 10:29:30+00:00   
7389      2    103007  Freguesia de jacarepaguá 2023-09-25 07:44:30+00:00   

                      data_fim  prazo  \
0    2023-11-01 11:37:06+00:00  Curto   
1    2023-11-01 18:19:18+00:00  Curto   
2    2023-11-01 07:35:59+00:00  Curto   
3    2023-11-01 13:05:55+00:00  Curto   
4    2023-11-02 22:08:34+00:00  Curto   
...                        ...    ...   
7385 2023-09-10 17:25:41+00:00  Curto   
7386 2023-09-01 06:11:50+00:00  Curto   
7387 2023-09-06 09:13:36+00:00  Curto   
7388 2023-09-19 11:42:58+00:00  Curto   
7389 2023-09-25 08:28:33+00:00  Curto   

                                              descricao gravidade   latitude  \
0     Av. min. ivan lins - alt. ponte da joatinga - ...     Baixo -23.007138   
1     Estr. grajaú/jpa - alt. km 4,5 - eng. novo - s...     Baixo -22.923714   
2     Av. brasil - alt. guadalupe - guadalupe - sent...     Baixo -22.861892   
3           Linha amarela - alt. pedágio - sent. fundão     Baixo -22.908814   
4     Av. das américas - alt. n° 4059 - barra da tij...     Baixo -23.000598   
...                                                 ...       ...        ...   
7385  Viaduto do gasômetro - alt. rodoviária - santo...     Medio -22.898193   
7386  Elevado paulo de frontin  - rio comprido - sen...     Medio -22.919729   
7387        Linha amarela - cidade de deus - sent. orla     Medio -22.947957   
7388          Túnel rebouças - 2° galeria - sent. lagoa     Medio -22.949183   
7389          Túnel rebouças - 2a galeria - sent. lagoa     Medio -22.949183   

      longitude   status      tipo data_particao      coloracao  raio  
0    -43.305252  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
1    -43.258467  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
2    -43.549415  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
3    -43.314814  Fechado  Primario    2023-11-01  [255, 255, 0]    50  
4    -43.354677  Fechado  Primario    2023-11-02  [255, 255, 0]    50  
...         ...      ...       ...           ...            ...   ...  
7385 -43.211672  Fechado  Primario    2023-09-10  [255, 165, 0]    50  
7386 -43.209590  Fechado  Primario    2023-09-01  [255, 165, 0]    50  
7387 -43.355575  Fechado  Primario    2023-09-06  [255, 165, 0]    50  
7388 -43.350800  Fechado  Primario    2023-09-19  [255, 165, 0]    50  
7389 -43.350800  Fechado  Primario    2023-09-25  [255, 165, 0]    50  

[7390 rows x 15 columns]

In [19]:
camera_inicial = pdk.ViewState(
    latitude = -22.9035, 
    longitude = -43.4096, 
    zoom = 9.3, 
    max_zoom = 16, 
    pitch = 0, 
    bearing = 0
)

base = pdk.Layer(
    "PolygonLayer",
    stroked = False,
    get_polygon = "-",
    get_fill_color = [0, 0, 0, 20],
)

ocorrencias = pdk.Layer(
    "ScatterplotLayer",
    chamados_rjcor[["latitude", "longitude", "coloracao", "raio", "bairro", "data_inicio", "gravidade", "descricao", "status"]],
    get_position = ["longitude", "latitude"],
    auto_highlight = True,
    get_radius = "raio",
    get_fill_color = "coloracao",
    pickable = True
)

r = pdk.Deck(
    layers = [base, ocorrencias], 
    initial_view_state = camera_inicial,
    tooltip = {"html": "<b>Bairro:</b> {bairro}<br><b>Data de inicio:</b> {data_inicio}"\
               "<br><b>Gravidade:</b> {gravidade}<br><b>Endereço:</b> {descricao}"\
               "<br><b>Situação:</b> {status}",
               "style": {
                  "backgroundColor": "steelblue",
                  "color": "white"
                        }
              },
    map_style = "dark"
)

r.to_html("geojson_layer.html")